In [1]:
import pandas as pd
import geopandas as gpd
from calitp_data_analysis.sql import query_sql
from calitp_data_analysis.gcs_geopandas import GCSGeoPandas
from calitp_data_analysis.geography_utils import CA_NAD83Albers_m, WGS84
gcsgp = GCSGeoPandas()
from shared_utils import gtfs_utils_v2, rt_utils

import utils
import update_vars

import altair as alt

In [2]:
import numpy as np

In [ ]:
import shapely

In [3]:
import importlib
importlib.reload(utils)
importlib.reload(update_vars)

<module 'update_vars' from '/home/jovyan/data-analyses/thruway_intercity_bus/update_vars.py'>

In [4]:
! pip install "vegafusion[embed]>=1.5.0"
! pip install "vl-convert-python>=1.6.0"

  Using cached vegafusion-2.0.2-cp39-abi3-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (1.1 kB)
  Using cached arro3_core-0.6.2-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (363 bytes)
Using cached vegafusion-2.0.2-cp39-abi3-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (20.5 MB)
Using cached arro3_core-0.6.2-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (2.8 MB)
  Using cached vl_convert_python-1.8.0-cp37-abi3-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (5.2 kB)
Using cached vl_convert_python-1.8.0-cp37-abi3-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (33.0 MB)


In [5]:
alt.data_transformers.enable("vegafusion")

DataTransformerRegistry.enable('vegafusion')

# Create utils to get stop sequence and distance info for ridership charts

* currently blocked on warehouse issues for SJJPA feed, could maybe do CC on `gtfs_funnel` cached files...

In [6]:
analysis_date = update_vars.ANALYSIS_DATE

In [7]:
ca = gcsgp.read_parquet('gs://calitp-analytics-data/data-analyses/high_quality_transit_areas/ca_boundary.parquet')

## New SJJPA San Joaquins feed

In [8]:
feeds = gtfs_utils_v2.schedule_daily_feed_to_gtfs_dataset_name(analysis_date)

In [39]:
sanj = feeds.query('name == "Amtrak San Joaquins Schedule"')

In [40]:
sanj

key       date  \
77  2b538004ce62dd20b1c326745da7834f 2025-09-10   

                            feed_key        feed_timezone  \
77  d9e1e77d0754b712fc608741ae3836f5  America/Los_Angeles   

                                           base64_url  \
77  aHR0cHM6Ly9kMzR0aXc2NG41ejRvaC5jbG91ZGZyb250Lm...   

                    gtfs_dataset_key                          name      type  \
77  524ea6209600e9a2de34a02cf9068729  Amtrak San Joaquins Schedule  schedule   

   regional_feed_type  
77               None

In [41]:
sanj_shapes = gtfs_utils_v2.get_shapes(analysis_date, operator_feeds=sanj.feed_key, shape_cols=update_vars.shape_cols)
sanj_shapes = sanj_shapes.to_crs(CA_NAD83Albers_m)
sanj_shapes = sanj_shapes.assign(length_meters = sanj_shapes.geometry.length)

/opt/conda/lib/python3.11/site-packages/sqlalchemy_bigquery/_types.py:101: SAWarning: Did not recognize type 'GEOGRAPHY' of column 'pt_array'
  sqlalchemy.util.warn(


In [42]:
sanj_trips = gtfs_utils_v2.get_trips(analysis_date, operator_feeds=sanj.feed_key, trip_cols=update_vars.trip_cols).query('route_type == "3"')

In [43]:
sanj_stops = gtfs_utils_v2.get_stops(analysis_date, operator_feeds=sanj.feed_key, stop_cols=update_vars.stop_cols).to_crs(CA_NAD83Albers_m)

/opt/conda/lib/python3.11/site-packages/sqlalchemy_bigquery/_types.py:101: SAWarning: Did not recognize type 'GEOGRAPHY' of column 'pt_geom'
  sqlalchemy.util.warn(


In [44]:
sanj_st = gtfs_utils_v2.get_stop_times(analysis_date, operator_feeds=sanj.feed_key, get_df=True,
                                      trip_df = sanj_trips, stop_time_cols=update_vars.stop_time_cols)

/opt/conda/lib/python3.11/site-packages/sqlalchemy_bigquery/_types.py:101: SAWarning: Did not recognize type 'INTERVAL' of column 'arrival_time_interval'
  sqlalchemy.util.warn(
/opt/conda/lib/python3.11/site-packages/sqlalchemy_bigquery/_types.py:101: SAWarning: Did not recognize type 'INTERVAL' of column 'departure_time_interval'
  sqlalchemy.util.warn(
/opt/conda/lib/python3.11/site-packages/sqlalchemy_bigquery/_types.py:101: SAWarning: Did not recognize type 'INTERVAL' of column 'start_pickup_drop_off_window_interval'
  sqlalchemy.util.warn(
/opt/conda/lib/python3.11/site-packages/sqlalchemy_bigquery/_types.py:101: SAWarning: Did not recognize type 'INTERVAL' of column 'end_pickup_drop_off_window_interval'
  sqlalchemy.util.warn(


In [45]:
sanj_shapes_trip_info = (sanj_shapes.merge(sanj_trips.drop_duplicates(subset=['shape_array_key']), on = ['shape_array_key', 'feed_key'])
                            .drop(columns=['base64_url', 'regional_feed_type', 'block_id',
                                           'route_desc', 'agency_id', 'network_id',
                                          'route_key'])
                        )

In [46]:
sort_cols = ['route_id', 'direction_id']

In [47]:
def longest_by_route_dir(shape_trip_df):
    #  https://github.com/cal-itp/data-analyses/blob/1abcd5d05163176567f644f6f245366dd9cc53fc/rt_segment_speeds/segment_speed_utils/gtfs_schedule_wrangling.py#L426
    df = (shape_trip_df.query('route_type == "3"')
     .sort_values(sort_cols + ['length_meters'], ascending=[True for i in sort_cols] + [False])
     .drop_duplicates(subset=sort_cols)
     .reset_index(drop=True)
    )
    return df

In [48]:
sanj_long_shapes = longest_by_route_dir(sanj_shapes_trip_info)

### translate stop_id to ridership data stop_id

In [50]:
source_ridership = pd.read_excel(update_vars.RIDERSHIP_PATH)
source_ridership = source_ridership.assign(od = source_ridership.orig + '->' + source_ridership.dest)
source_ridership = source_ridership.assign(route_short_name = source_ridership.ca_bus_route.str.replace('Rt', 'Route'))
source_ridership = source_ridership.query('trip_year == 2025 & trip_month == 4') ## TODO trends, etc

strip_zero = lambda route_str: ' '.join([x.lstrip('0') for x in route_str.split(' ')])
rider_to_gtfs_dict = {'Route 1A': 'Route 1', 'Route 1B': 'Route 1', 'Route 1C': 'Route 1c'}
rider_to_gtfs = lambda route_str: rider_to_gtfs_dict[route_str] if route_str in rider_to_gtfs_dict.keys() else route_str

source_ridership = source_ridership.assign(route_short_name = source_ridership.route_short_name.map(strip_zero).map(rider_to_gtfs))

In [54]:
bus_stops = sanj_st.stop_id.unique()

In [55]:
get_ridership_unique_stops = lambda df: np.union1d(df.orig, df.dest)

In [56]:
rider_stops = get_ridership_unique_stops(source_ridership)

In [57]:
sanj_bus_to_rider_stops = dict(zip(bus_stops, [x[1:] for x in bus_stops]))
sanj_bus_to_rider_stops['bLOS'] = 'LAX'

In [59]:
# pd.Series(sanj_bus_to_rider_stops.values()).isin(pd.Series(rider_stops)).value_counts()

# gtfs_no_rider_data = pd.Series(sanj_bus_to_rider_stops.values())[~pd.Series(sanj_bus_to_rider_stops.values()).isin(pd.Series(rider_stops))]
# gtfs_no_rider_data #  OK -- all either served by RABA/YARTS or outside CA...

### make chart tables

In [60]:
rt1_test = sanj_long_shapes.query('route_id == "1"')

In [61]:
rt1_test

feed_key                   shape_array_key  \
0  d9e1e77d0754b712fc608741ae3836f5  fddc98c94a7294a6a4e4c0c02cb75690   
1  d9e1e77d0754b712fc608741ae3836f5  dddf1c13185f9f23ab5dea9f85579855   

                                            geometry  length_meters  \
0  LINESTRING (265701.090 -584418.173, 265726.924...  404935.670408   
1  LINESTRING (89964.411 -293278.458, 89963.886 -...  404265.833098   

                  trip_instance_key trip_id trip_short_name  \
0  5322f590222c5c245f0b996ce8d45de0    5811          AMTthr   
1  ba1722adf2f21329a76ec5d85a01890d    5885          AMTthr   

                           name                  gtfs_dataset_key  \
0  Amtrak San Joaquins Schedule  524ea6209600e9a2de34a02cf9068729   
1  Amtrak San Joaquins Schedule  524ea6209600e9a2de34a02cf9068729   

  service_date  direction_id route_id route_type route_short_name  \
0   2025-09-10             0        1          3          Route 1   
1   2025-09-10             1        1          3          Route 1   

                                     route_long_name shape_id  
0  Fresno/Bekersfield - Los Angeles- SantaAna - O...     jfy7  
1  Fresno/Bekersfield - Los Angeles- SantaAna - O...     xurp

In [62]:
bus_st = sanj_st.merge(sanj_trips[['trip_id', 'direction_id', 'route_id', 'route_short_name',
                                   'shape_array_key', 'shape_id']], on='trip_id')

In [63]:
bus_st = pd.merge(sanj_stops[['stop_id', 'geometry']], bus_st, on='stop_id')
bus_st = bus_st.assign(amtrak_stop = bus_st.stop_id.map(sanj_bus_to_rider_stops)).sort_values(['trip_id', 'stop_sequence'])

In [65]:
def transform_gtfs_info(one_direction_st_df, shape_geom):
    
    mi_range = lambda row: np.arange(row.stop_miles, row.next_miles) if not np.isnan(row.stop_miles) and not np.isnan(row.next_miles) else None
    df = one_direction_st_df.assign(stop_meters = one_direction_st_df.geometry.map(lambda x: shape_geom.project(x)))
    df = df.assign(stop_miles = np.round((df.stop_meters / rt_utils.METERS_PER_MILE), 0).astype(int))
    df = df.assign(next_miles = df.stop_miles.shift(-1))
    df = df.assign(mile_range = df.apply(mi_range, axis=1))

    return df

In [66]:
def explode_gtfs_info(gtfs_info_df):
    
    gtfs_info_df = gtfs_info_df[['amtrak_stop', 'stop_sequence','route_id',
                     'route_short_name', 'shape_id', 'direction_id',
                        'mile_range']].explode(column='mile_range').rename(columns={'mile_range': 'route_mileage'})
    return gtfs_info_df

In [67]:
def stop_sequence_dict_and_direction_id(gtfs_info_df):
    df = gtfs_info_df[['amtrak_stop', 'stop_sequence', 'direction_id']].drop_duplicates()
    assert len(df.direction_id.unique()) == 1
    direction_id = df.direction_id.iloc[0]
    sequence_dict = df[['amtrak_stop', 'stop_sequence']].set_index('amtrak_stop').stop_sequence.to_dict()
    
    return sequence_dict, direction_id

In [86]:
def determine_direction(row, gtfs_info_df):
    
    sequence_dict, direction_id = stop_sequence_dict_and_direction_id(gtfs_info_df)
    if sequence_dict[row.orig] < sequence_dict[row.dest]:
        return direction_id
    elif sequence_dict[row.orig] > sequence_dict[row.dest]:
        return 1 - direction_id
    else:
        return ''

In [87]:
def running_ridership(df, gtfs_info_df):
    
    sequence_dict, direction_id = stop_sequence_dict_and_direction_id(gtfs_info_df)
    running_df = []
    for stn in sequence_dict.keys():
        stn_seq = sequence_dict[stn]
        if stn_seq < max(sequence_dict.values()):
            df_at = df.query('orig_seq <= @stn_seq & dest_seq > @stn_seq').assign(departing_station = stn)
            running_df += [df_at]
    return pd.concat(running_df).sort_values('departing_station')

In [88]:
def filter_ridership(source_ridership_df, rider_bus_route, gtfs_info_df):
    
    sequence_dict, direction_id = stop_sequence_dict_and_direction_id(gtfs_info_df)
    df = source_ridership_df.query('ca_bus_route == @rider_bus_route & orig.isin(@gtfs_info_df.amtrak_stop) & dest.isin(@gtfs_info_df.amtrak_stop)')
    df = df.assign(direction_id = df.apply(determine_direction, axis=1, gtfs_info_df = gtfs_info_df),
                orig_seq = df.orig.apply(lambda x: sequence_dict[x]),
                dest_seq = df.dest.apply(lambda x: sequence_dict[x])
                                  )
    df = df.query('direction_id == @direction_id')
    return df

In [89]:
def chart_rider_flow(with_distance_df):
    
    flow = alt.Chart(with_distance_df).mark_area().encode(
    alt.X('route_mileage:Q'),
    alt.Y('sum(ridership):Q'),
    color='od',
    tooltip = ['departing_station', 'od', 'ridership']
        ).properties(width = with_distance_df.route_mileage.max() * 3)
    
    return flow

In [90]:
one_dir = bus_st.query('trip_id == @rt1_test.trip_id.iloc[0]')

In [91]:
gtfs_info_df = transform_gtfs_info(one_dir, rt1_test.geometry.iloc[0])

In [92]:
gtfs_info_df = explode_gtfs_info(gtfs_info_df)

In [93]:
rider_one_rt_dir = filter_ridership(source_ridership, 'Rt 1A', gtfs_info_df)

In [94]:
rider_one_rt_dir = running_ridership(rider_one_rt_dir, gtfs_info_df)

In [95]:
with_distance = rider_one_rt_dir.merge(gtfs_info_df[['amtrak_stop', 'route_mileage']], left_on = 'departing_station', right_on = 'amtrak_stop')

In [96]:
with_distance.route_mileage = with_distance.route_mileage.astype(int)

In [97]:
chart_rider_flow(with_distance)

alt.Chart(...)

#### opposite direction

In [98]:
one_dir = bus_st.query('trip_id == @rt1_test.trip_id.iloc[1]')

In [99]:
gtfs_info_df = transform_gtfs_info(one_dir, rt1_test.geometry.iloc[1])

In [100]:
gtfs_info_df = explode_gtfs_info(gtfs_info_df)

In [101]:
rider_one_rt_dir = filter_ridership(source_ridership, 'Rt 1A', gtfs_info_df)

In [102]:
rider_one_rt_dir = running_ridership(rider_one_rt_dir, gtfs_info_df)

In [103]:
with_distance = rider_one_rt_dir.merge(gtfs_info_df[['amtrak_stop', 'route_mileage']], left_on = 'departing_station', right_on = 'amtrak_stop')

In [104]:
chart_rider_flow(with_distance.dropna())

alt.Chart(...)

In [105]:
source_ridership.groupby('od')[['ridership']].sum().reset_index().query('od == "BFD->LAX"')

od  ridership
36  BFD->LAX       7637

## Route 1C

In [106]:
rt1c_test = sanj_long_shapes.query('route_id == "1c"')

#### one direction

In [107]:
one_dir = bus_st.query('trip_id == @rt1c_test.trip_id.iloc[0]')

In [108]:
gtfs_info_df = transform_gtfs_info(one_dir, rt1c_test.geometry.iloc[0])

In [109]:
gtfs_info_df = explode_gtfs_info(gtfs_info_df)

In [110]:
rider_one_rt_dir = filter_ridership(source_ridership, 'Rt 1C', gtfs_info_df)

In [111]:
rider_one_rt_dir = running_ridership(rider_one_rt_dir, gtfs_info_df)

In [112]:
with_distance = rider_one_rt_dir.merge(gtfs_info_df[['amtrak_stop', 'route_mileage']], left_on = 'departing_station', right_on = 'amtrak_stop')

In [113]:
chart_rider_flow(with_distance.dropna())

alt.Chart(...)

#### other direction

In [114]:
one_dir = bus_st.query('trip_id == @rt1c_test.trip_id.iloc[1]')

In [115]:
one_dir.loc[531, 'amtrak_stop'] = 'SMN' #  is this a GTFS error?

In [116]:
gtfs_info_df = transform_gtfs_info(one_dir, rt1c_test.geometry.iloc[1])

In [117]:
gtfs_info_df = explode_gtfs_info(gtfs_info_df)

In [118]:
sequence_dict, direction_id = stop_sequence_dict_and_direction_id(gtfs_info_df)

In [119]:
sequence_dict

{'BFD': 0, 'NHL': 1, 'BUR': 2, 'VNC': 3, 'WES': 4, 'SMN': 5}

In [120]:
rider_one_rt_dir = filter_ridership(source_ridership, 'Rt 1C', gtfs_info_df)

In [121]:
rider_one_rt_dir = running_ridership(rider_one_rt_dir, gtfs_info_df)

In [122]:
with_distance = rider_one_rt_dir.merge(gtfs_info_df[['amtrak_stop', 'route_mileage']], left_on = 'departing_station', right_on = 'amtrak_stop')

In [123]:
chart_rider_flow(with_distance.dropna())

alt.Chart(...)

## Route 19

In [124]:
rt19_test = sanj_long_shapes.query('route_id == "19"')

#### one direction

In [125]:
one_dir = bus_st.query('trip_id == @rt19_test.trip_id.iloc[0]')

In [126]:
gtfs_info_df = transform_gtfs_info(one_dir, rt19_test.geometry.iloc[0])

In [127]:
gtfs_info_df = explode_gtfs_info(gtfs_info_df)

In [128]:
rider_one_rt_dir = filter_ridership(source_ridership, 'Rt 19', gtfs_info_df)

In [129]:
rider_one_rt_dir = running_ridership(rider_one_rt_dir, gtfs_info_df)

In [130]:
with_distance = rider_one_rt_dir.merge(gtfs_info_df[['amtrak_stop', 'route_mileage']], left_on = 'departing_station', right_on = 'amtrak_stop')

In [131]:
chart_rider_flow(with_distance.dropna())

alt.Chart(...)

#### other direction

In [132]:
one_dir = bus_st.query('trip_id == @rt19_test.trip_id.iloc[1]')

In [133]:
gtfs_info_df = transform_gtfs_info(one_dir, rt19_test.geometry.iloc[1])

In [134]:
gtfs_info_df = explode_gtfs_info(gtfs_info_df)

In [135]:
sequence_dict, direction_id = stop_sequence_dict_and_direction_id(gtfs_info_df)

In [136]:
sequence_dict

{'SNB': 0, 'RIV': 1, 'ONA': 2, 'CLM': 3, 'PAS': 4, 'LCA': 5, 'BFD': 6}

In [137]:
rider_one_rt_dir = filter_ridership(source_ridership, 'Rt 19', gtfs_info_df)

In [138]:
rider_one_rt_dir = running_ridership(rider_one_rt_dir, gtfs_info_df)

In [139]:
with_distance = rider_one_rt_dir.merge(gtfs_info_df[['amtrak_stop', 'route_mileage']], left_on = 'departing_station', right_on = 'amtrak_stop')

In [140]:
chart_rider_flow(with_distance.dropna())

alt.Chart(...)

## Route 7

In [141]:
rt7_test = sanj_long_shapes.query('route_id == "7"')

#### one direction

In [142]:
one_dir = bus_st.query('trip_id == @rt7_test.trip_id.iloc[0]')

In [143]:
gtfs_info_df = transform_gtfs_info(one_dir, rt7_test.geometry.iloc[0])

In [144]:
gtfs_info_df = explode_gtfs_info(gtfs_info_df)

In [145]:
rider_one_rt_dir = filter_ridership(source_ridership, 'Rt 07', gtfs_info_df)

In [146]:
rider_one_rt_dir = running_ridership(rider_one_rt_dir, gtfs_info_df)

In [147]:
with_distance = rider_one_rt_dir.merge(gtfs_info_df[['amtrak_stop', 'route_mileage']], left_on = 'departing_station', right_on = 'amtrak_stop')

In [148]:
chart_rider_flow(with_distance.dropna())

alt.Chart(...)

#### other direction

In [149]:
one_dir = bus_st.query('trip_id == @rt7_test.trip_id.iloc[1]')

In [150]:
gtfs_info_df = transform_gtfs_info(one_dir, rt7_test.geometry.iloc[1])

In [151]:
gtfs_info_df = explode_gtfs_info(gtfs_info_df)

In [152]:
sequence_dict, direction_id = stop_sequence_dict_and_direction_id(gtfs_info_df)

In [153]:
rider_one_rt_dir = filter_ridership(source_ridership, 'Rt 07', gtfs_info_df)

In [154]:
rider_one_rt_dir = running_ridership(rider_one_rt_dir, gtfs_info_df)

In [155]:
with_distance = rider_one_rt_dir.merge(gtfs_info_df[['amtrak_stop', 'route_mileage']], left_on = 'departing_station', right_on = 'amtrak_stop')

In [156]:
chart_rider_flow(with_distance)

alt.Chart(...)